## 217 

* issue [#217](https://github.com/salgo60/Stockholm_Archipelago_Trail/issues/217)
* den här Noteboken [217_SAT_wikipedia_OSM.ipynb](https://github.com/salgo60/Stockholm_Archipelago_Trail/blob/main/notebook/217_SAT_wikipedia_OSM.ipynb)
* [Karta SAT_217_Wikipedia_OSM_latest](https://raw.githack.com/salgo60/Stockholm_Archipelago_Trail/main/notebook/output/SAT_217_Wikipedia_OSM_latest.html)


In [1]:
import time

from datetime import datetime

now = datetime.now()
timestamp = now.timestamp()

start_time = time.time()
print("Start:", datetime.now().strftime("%Y-%m-%d %H:%M:%S"))

Start: 2025-10-02 15:03:32


In [2]:
# SAT DashboarMap – Social Media, Corridor Visualization & OSM Caching
# 1) All Wikidata objects related to the trail via P6104=Q134294510, including social media + Google Maps links
# 2) OSM objects fetched once via bounding box (cached), filtered by ~300 m corridor
# 3) Toggleable layers: Wikidata, Wikidata with social media, OSM, OSM with social media, Trail, Corridor
# 4) About box, Legend box, Collapsible Stats box

import os, json, requests
import folium
from folium import FeatureGroup
from folium.plugins import MousePosition, Fullscreen, MeasureControl
from shapely.geometry import LineString, MultiLineString, Polygon, Point
from shapely.ops import unary_union, transform as shp_transform
from pyproj import Transformer
import geopandas as gpd
from branca.element import MacroElement
from jinja2 import Template

# ========================
# Config
# ========================
WD_SPARQL_ENDPOINT = "https://query.wikidata.org/sparql"
WD_PROP = "P6104"
WD_VALUE = "Q134294510"         # Stockholm Archipelago Trail

BUFFER_METERS_EACH_SIDE = 150
GEOJSON_PATH = "SAT_full.geojson"
OSM_CACHE_FILE = "osm_cache.json"

MAP_CENTER = [59.5, 18.8]
MAP_ZOOM = 9

# ========================
# Helpers
# ========================

def wikidata_items_with_social(lang="sv"):
    query = f"""
    SELECT ?item ?itemLabel ?itemDescription ?coord
           ?website ?commonscat ?image ?svwiki
           ?naturkartan ?inatplace ?instaplace ?gmapid
    WHERE {{
      ?item wdt:{WD_PROP} wd:{WD_VALUE} .
      OPTIONAL {{ ?item wdt:P625 ?coord }}
      OPTIONAL {{ ?item wdt:P856 ?website }}
      OPTIONAL {{ ?item wdt:P373 ?commonscat }}
      OPTIONAL {{ ?item wdt:P18 ?image }}
      OPTIONAL {{ ?item wdt:P10467 ?naturkartan }}
      OPTIONAL {{ ?item wdt:P7471 ?inatplace }}
      OPTIONAL {{ ?item wdt:P4173 ?instaplace }}
      OPTIONAL {{ ?item wdt:P3749 ?gmapid }}
      OPTIONAL {{
        ?svwiki schema:about ?item ;
                schema:isPartOf <https://sv.wikipedia.org/> .
      }}
      SERVICE wikibase:label {{ bd:serviceParam wikibase:language "{lang},en". }}
    }}
    """
    r = requests.get(WD_SPARQL_ENDPOINT, params={"query": query, "format": "json"}, headers={"User-Agent": "SAT-Dashboard/1.0"})
    r.raise_for_status()
    data = r.json()
    out = []
    for b in data["results"]["bindings"]:
        item = b["item"]["value"]
        label = b.get("itemLabel", {}).get("value")
        desc = b.get("itemDescription", {}).get("value")
        coord = b.get("coord", {}).get("value") if "coord" in b else None
        latlon = None
        if coord:
            try:
                coord_clean = coord.replace("Point(", "").replace(")", "")
                lon, lat = map(float, coord_clean.split(" "))
                latlon = [lat, lon]
            except Exception:
                latlon = None
        out.append({
            "item": item,
            "label": label,
            "description": desc,
            "latlon": latlon,
            "website": b.get("website", {}).get("value"),
            "commonscat": b.get("commonscat", {}).get("value"),
            "image": b.get("image", {}).get("value"),
            "svwiki": b.get("svwiki", {}).get("value"),
            "naturkartan": b.get("naturkartan", {}).get("value"),
            "inatplace": b.get("inatplace", {}).get("value"),
            "instaplace": b.get("instaplace", {}).get("value"),
            "gmapid": b.get("gmapid", {}).get("value"),
        })
    return out


def overpass(query: str):
    url = "https://overpass-api.de/api/interpreter"
    r = requests.post(url, data={"data": query}, headers={"User-Agent": "SAT-Dashboard/1.0"})
    r.raise_for_status()
    return r.json()

def get_trail_geometry_from_geojson(path=GEOJSON_PATH):
    gdf = gpd.read_file(path)
    lines = []
    for geom in gdf.geometry:
        if isinstance(geom, LineString):
            lines.append(geom)
        elif isinstance(geom, MultiLineString):
            lines.extend(list(geom.geoms))
    return lines

def corridor_from_lines_wgs84(lines, buffer_m):
    to_utm = Transformer.from_crs("EPSG:4326", "EPSG:32633", always_xy=True).transform
    to_wgs = Transformer.from_crs("EPSG:32633", "EPSG:4326", always_xy=True).transform
    utm_lines = [shp_transform(to_utm, ln) for ln in lines]
    merged = unary_union(utm_lines)
    corridor_utm = merged.buffer(buffer_m)
    corridor_wgs84 = shp_transform(to_wgs, corridor_utm)
    return corridor_wgs84

def fetch_osm_bbox(minlat, minlon, maxlat, maxlon):
    q = f"""
    [out:json][timeout:300];
    (
      node[amenity]({minlat},{minlon},{maxlat},{maxlon});
      way[amenity]({minlat},{minlon},{maxlat},{maxlon});
      node[tourism]({minlat},{minlon},{maxlat},{maxlon});
      way[tourism]({minlat},{minlon},{maxlat},{maxlon});
      node[natural]({minlat},{minlon},{maxlat},{maxlon});
      way[natural]({minlat},{minlon},{maxlat},{maxlon});
      node[highway]({minlat},{minlon},{maxlat},{maxlon});
      way[highway]({minlat},{minlon},{maxlat},{maxlon});
    );
    out body geom qt;
    >; out skel qt;
    """
    return overpass(q)
def load_or_fetch_filtered_osm(minlat, minlon, maxlat, maxlon, corridor_geom,
                               reload_osm=False,
                               raw_cache_file=OSM_CACHE_FILE,
                               filtered_cache_file="osm_filtered_cache.json"):
    # If filtered cache exists and reload is False → load it directly
    if not reload_osm and os.path.exists(filtered_cache_file):
        print(f"Loading filtered OSM data from cache: {filtered_cache_file}")
        with open(filtered_cache_file, "r", encoding="utf-8") as f:
            filtered_data = json.load(f)
        from_cache = True
        return filtered_data, from_cache
    
    # Otherwise, get raw data (from cache or Overpass)
    raw_data, raw_from_cache = load_or_fetch_osm(minlat, minlon, maxlat, maxlon,
                                                 reload_osm=reload_osm,
                                                 cache_file=raw_cache_file)
    
    # Filter corridor
    print("Filtering OSM raw elements inside corridor…")
    filtered_elements = []
    seen = set()
    for el in raw_data.get("elements", []):
        el_id = (el.get("type"), el.get("id"))
        if el_id in seen:
            continue
        seen.add(el_id)
        tags = el.get("tags", {})
        if not tags:
            continue
        if el["type"] == "node":
            lat, lon = el.get("lat"), el.get("lon")
            if lat is not None and lon is not None and corridor_geom.intersects(Point(lon, lat)):
                filtered_elements.append(el)
        elif el["type"] == "way" and "geometry" in el:
            coords = [(pt["lon"], pt["lat"]) for pt in el["geometry"]]
            if len(coords) >= 2 and corridor_geom.intersects(LineString(coords)):
                filtered_elements.append(el)
    
    filtered_data = {"elements": filtered_elements}
    
    # Save filtered cache
    with open(filtered_cache_file, "w", encoding="utf-8") as f:
        json.dump(filtered_data, f)
    print(f"Saved filtered OSM data to {filtered_cache_file} (count={len(filtered_elements)})")
    
    return filtered_data, False

# --- Formatters for nicer popups ---

# --- Improved Popup Formatters with Icons, Styling & Commons Thumbnails ---

import datetime
import pytz


def format_opening_hours(oh_string, tz="Europe/Stockholm"):
    """Parse OSM-style opening_hours and return status text"""
    try:
        oh = opening_hours.OpeningHours(oh_string)
        now = datetime.datetime.now(pytz.timezone(tz))
        if oh.is_open(now):
            return f"🟢 Open now ({oh_string})"
        else:
            return f"🔴 Closed now ({oh_string})"
    except Exception:
        return f"⏰ {oh_string}"


def format_osm_popup(tags, el_type=None, el_id=None):
    name = tags.get("name", "(no name)")

    # Prefer Wikimedia Commons image if available
    img_html = ""
    if 'image' in tags:
        img_html = f"<img src='{tags['image']}' width='200' style='margin-bottom:6px;'><br>"
    elif 'wikimedia_commons' in tags:
        commons_name = tags['wikimedia_commons'].replace(" ", "_")
        img_html = f"<img src='https://commons.wikimedia.org/wiki/Special:FilePath/{commons_name}?width=200' width='200' style='margin-bottom:6px;'><br>"

    # Opening hours
    oh_html = ""
    if "opening_hours" in tags:
        oh_html = f"<p>{format_opening_hours(tags['opening_hours'])}</p>"

    # Build links
    links = []
    if 'website' in tags:
        links.append(f"🌐 <a href='{tags['website']}' target='_blank'>Website</a>")
    if 'wikidata' in tags:
        links.append(f"🗺️ <a href='https://www.wikidata.org/wiki/{tags['wikidata']}' target='_blank'>Wikidata</a>")
    if 'wikimedia_commons' in tags:
        links.append(f"🖼️ <a href='https://commons.wikimedia.org/wiki/{tags['wikimedia_commons']}' target='_blank'>Commons</a>")
    if 'contact:facebook' in tags:
        links.append(f"👥 <a href='{tags['contact:facebook']}' target='_blank'>Facebook</a>")
    if 'contact:instagram' in tags:
        links.append(f"📷 <a href='{tags['contact:instagram']}' target='_blank'>Instagram</a>")
    if 'contact:twitter' in tags:
        links.append(f"🐦 <a href='{tags['contact:twitter']}' target='_blank'>Twitter/X</a>")
    if el_type and el_id:
        links.append(f"🔗 <a href='https://www.openstreetmap.org/{el_type}/{el_id}' target='_blank'>OSM</a>")

    html = f"""
    <div style='min-width:240px;font-family:sans-serif;font-size:13px;'>
      <h4 style='margin:0 0 6px 0;'>{name}</h4>
      {img_html}
      <p style='margin:0 0 6px 0;'>{tags.get('information','')}</p>
      {oh_html}
      <p style='margin:0;'>{' | '.join(links)}</p>
    </div>
    """
    return html



def format_wikidata_popup(it):
    label = it.get("label") or it["item"].split("/")[-1]
    desc = it.get("description") or ""

    img_html = ""
    if it.get("image"):
        img_html = f"<img src='{it['image']}' width='200' style='margin-bottom:6px;'><br>"
    elif it.get("commonscat"):
        cat = it['commonscat'].replace(" ", "_")
        img_html = f"<img src='https://commons.wikimedia.org/wiki/Special:FilePath/{cat}?width=200' width='200' style='margin-bottom:6px;'><br>"

    links = [f"🗺️ <a href='{it['item']}' target='_blank'>Wikidata</a>"]
    if it.get("svwiki"): links.append(f"📖 <a href='{it['svwiki']}' target='_blank'>Wikipedia</a>")
    if it.get("commonscat"): links.append(f"🖼️ <a href='https://commons.wikimedia.org/wiki/Category:{it['commonscat']}' target='_blank'>Commons</a>")
    if it.get("website"): links.append(f"🌐 <a href='{it['website']}' target='_blank'>Website</a>")
    if it.get("naturkartan"): links.append(f"🧭 <a href='https://naturkartan.se/sv/places/{it['naturkartan']}' target='_blank'>Naturkartan</a>")
    if it.get("inatplace"): links.append(f"🌱 <a href='https://www.inaturalist.org/places/{it['inatplace']}' target='_blank'>iNaturalist</a>")
    if it.get("instaplace"): links.append(f"📍 <a href='https://www.instagram.com/explore/locations/{it['instaplace']}/' target='_blank'>Instagram Place</a>")
    if it.get("instagram"): links.append(f"📷 <a href='https://www.instagram.com/{it['instagram']}/' target='_blank'>Instagram</a>")
    if it.get("twitter"): links.append(f"🐦 <a href='https://x.com/{it['twitter']}' target='_blank'>Twitter/X</a>")
    if it.get("facebook"): links.append(f"👥 <a href='https://www.facebook.com/{it['facebook']}' target='_blank'>Facebook</a>")
    if it.get("gmapid"): links.append(f"📍 <a href='https://www.google.com/maps?cid={it['gmapid']}' target='_blank'>Google Maps</a>")

    html = f"""
    <div style='min-width:240px;font-family:sans-serif;font-size:13px;'>
        <h4 style='margin:0 0 6px 0;'>{label}</h4>
        {img_html}
        <p style='margin:0 0 6px 0;'><em>{desc}</em></p>
        <p style='margin:0;'>{' | '.join(links)}</p>
    </div>
    """
    return html


# --- Update trail layer to include official links ---
# --- Trail layer ---
def add_trail_layer(m, lines, group_name="SAT trail (from GeoJSON)"):
    fg = FeatureGroup(name=group_name, show=True)
    for ln in lines:
        latlons = [(y, x) for x, y in ln.coords]
        popup_html = """
        <div style='font-family:sans-serif;font-size:13px;'>
          <b>Stockholm Archipelago Trail</b><br>
          <a href='https://stockholmarchipelagotrail.com/' target='_blank'>🇸🇪 Official (Swedish)</a> |
          <a href='https://stockholmarchipelagotrail.com/en/' target='_blank'>🇬🇧 Official (English)</a>
        </div>
        """
        folium.PolyLine(latlons, weight=4, opacity=0.8, color="red",
                        popup=folium.Popup(popup_html, max_width=300)).add_to(fg)
    fg.add_to(m)
    return fg

# --- Replace in add layers ---

def add_osm_objects_layer(m: folium.Map, data, corridor_geom, group_name="OSM objects in 300 m corridor"):
    fg = FeatureGroup(name=group_name, show=True)
    seen = set()
    filtered_count = 0
    for el in data.get("elements", []):
        el_id = (el.get("type"), el.get("id"))
        if el_id in seen:
            continue
        seen.add(el_id)
        tags = el.get("tags", {})
        if not tags:
            continue
        if el["type"] == "node":
            lat, lon = el.get("lat"), el.get("lon")
            if lat is not None and lon is not None and corridor_geom.intersects(Point(lon, lat)):
                popup_html = format_osm_popup(tags)
                folium.CircleMarker([lat, lon], radius=3, color="black", popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
                filtered_count += 1
        elif el["type"] == "way" and "geometry" in el:
            coords = [(pt["lon"], pt["lat"]) for pt in el["geometry"]]
            if len(coords) >= 2:
                way_geom = LineString(coords)
                if corridor_geom.intersects(way_geom):
                    popup_html = popup_html = format_osm_popup(tags, el_type=el["type"], el_id=el["id"])
                    folium.PolyLine([(lat, lon) for lon, lat in coords], weight=2, color="gray",
                                    popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
                    filtered_count += 1
    fg.add_to(m)
    return filtered_count


def add_wikidata_layer(m: folium.Map, items, group_name="Wikidata (P6104)"):
    fg = FeatureGroup(name=group_name, show=True)
    for it in items:
        if it["latlon"]:
            lat, lon = it["latlon"]
            popup_html = format_wikidata_popup(it)
            folium.CircleMarker([lat, lon], radius=5, color="blue", fill=True, fill_opacity=0.7,
                                popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)

# ========================
# Map layers
# ========================

# --- OSM social media layer ---
def add_osm_social_layer(m: folium.Map, data, corridor_geom, group_name="OSM with social media"):
    fg = FeatureGroup(name=group_name, show=False)
    for el in data.get("elements", []):
        tags = el.get("tags", {})
        if not tags:
            continue
        if any(k in tags for k in ["contact:facebook", "contact:instagram", "contact:twitter", "website"]):
            if el["type"] == "node":
                lat, lon = el.get("lat"), el.get("lon")
                if lat is not None and lon is not None and corridor_geom.intersects(Point(lon, lat)):
                    popup_html = format_osm_popup(tags, el_type=el["type"], el_id=el["id"])
                    folium.CircleMarker([lat, lon], radius=5, color="orange", fill=True, fill_opacity=0.8,
                                        popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)

# --- Wikidata with social media layer ---
def add_wikidata_social_layer(m: folium.Map, items, group_name="Wikidata with online presence"):
    fg = FeatureGroup(name=group_name, show=False)
    for it in items:
        if it["latlon"] and any([it.get("website"), it.get("inatplace"), it.get("instaplace"),
                                 it.get("gmapid"), it.get("naturkartan"),
                                 it.get("instagram"), it.get("twitter"), it.get("facebook")]):
            lat, lon = it["latlon"]
            popup_html = format_wikidata_popup(it)
            folium.CircleMarker([lat, lon], radius=6, color="purple", fill=True, fill_opacity=0.8,
                                popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)



# ========================
# UI Boxes
# ========================
class FixedMacroElement(MacroElement):
    def __init__(self, tpl, name="macro_element"):
        super().__init__()
        self._template = Template(tpl)
        self._name = name

def add_about_box(m, issue_number=217, map_name="SAT_wikipedia_OSM", repo="salgo60/Stockholm_Archipelago_Trail"):
    from datetime import datetime
    created_date = datetime.now().strftime("%Y-%m-%d %H:%M")
    issue_url = f"https://github.com/{repo}/issues/{issue_number}"

    tpl = f"""
    {{% macro html(this, kwargs) %}}
    <div style="position: fixed; top: 70px; left: 10px; z-index:9999;
                background: white; border:2px solid #666; border-radius:8px;
                padding: 8px; font-size:13px; box-shadow: 2px 2px 6px rgba(0,0,0,.3);
                max-width: 300px;">
      <details open>
        <summary style="cursor:pointer;font-weight:600;">ℹ️ About</summary>
        <div style="margin-top:6px;">
          <b>{map_name}</b><br>
          Created: {created_date}<br>
          Issue: <a href="{issue_url}" target="_blank">#{issue_number}</a><br>
          <div style="margin-top:6px;">
            <a href="https://youtu.be/_nbI8hkRAvA" target="_blank">▶️ video about the map</a><br>
            <a href="https://raw.githack.com/salgo60/Stockholm_Archipelago_Trail/main/notebook/output/SAT_ALL_IN_ONE_142_3_dashboard_latest.html" target="_blank">📊 SAT Dashboard</a><br>
            <a href="https://github.com/{repo}/issues?q=is%3Aissue" target="_blank">🐛 Project repo issues</a><br>
            <a href="https://www.openstreetmap.org/relation/19012437" target="_blank">🗺️ Trail on OSM</a><br>
            <a href="https://commons.wikimedia.org/wiki/Category:Stockholm_Archipelago_Trail" target="_blank">🖼️ Trail on Wikicommons</a><br>
            <a href="https://stockholmarchipelagotrail.com/" target="_blank">🌐 Official page</a><br>
            <a href="https://www.facebook.com/groups/2875020699552247" target="_blank">👥 Unofficial FB group</a><br>
            <a href="https://traveltrade.visitsweden.com/plan/news-sweden/Stockholm-Archipelago-Trail/" target="_blank">🇸🇪 Visit Sweden</a>
          </div>
        </div>
      </details>
    </div>
    {{% endmacro %}}
    """
    m.get_root().add_child(FixedMacroElement(tpl, name="about_box"))


def add_legend_box(m):
    legend_items = """
    🔵 Wikidata items<br>
    🟣 Wikidata with online presence<br>
    🔴 Trail line<br>
    🟩 Corridor polygon<br>
    ⚫ OSM objects<br>
    🟠 OSM with social media
    """
    tpl = f"""
    {{% macro html(this, kwargs) %}}
    <div style="position: fixed; bottom: 30px; left: 30px; z-index:9999;
                background: white; border:2px solid #666; border-radius:8px;
                padding: 8px; font-size:13px; box-shadow: 2px 2px 6px rgba(0,0,0,.3);
                max-width: 220px;">
      <details open>
        <summary style="cursor:pointer; font-weight:600;">📍 Legend</summary>
        <div style="margin-top:6px;">{legend_items}</div>
      </details>
    </div>
    {{% endmacro %}}
    """
    m.get_root().add_child(FixedMacroElement(tpl, name="legend_box"))

def add_stats_box(m, map_name: str, wd_count: int, osm_raw: int, osm_filtered: int, from_cache: bool = False):
    source = "cache" if from_cache else "Overpass"
    tpl = f"""
    {{% macro html(this, kwargs) %}}
    <div style="position: fixed; bottom: 30px; right: 30px; z-index:9999;
            background: white; border:2px solid #666; border-radius:8px;
            padding: 8px; font-size:13px; box-shadow: 2px 2px 6px rgba(0,0,0,.3);
            max-width: 260px;">
        <details>
            <summary style="cursor:pointer;font-weight:600;">📊 Status</summary>
            <div style="margin-top:6px;">
              <b>{map_name}</b><br>
              Wikidata items: {wd_count}<br>
              OSM fetched: {osm_raw}<br>
              OSM in corridor: {osm_filtered}<br>
              Source: {source}
            </div>
        </details>
    </div>
    {{% endmacro %}}
    """
    m.get_root().add_child(FixedMacroElement(tpl, name="stats_box"))

def add_osm_with_opening_hours(m: folium.Map, data, corridor_geom, group_name="OSM with opening hours"):
    fg = FeatureGroup(name=group_name, show=False)
    for el in data.get("elements", []):
        tags = el.get("tags", {})
        if not tags:
            continue
        if "opening_hours" not in tags:
            continue  # skip if no hours

        if el["type"] == "node":
            lat, lon = el.get("lat"), el.get("lon")
            if lat is not None and lon is not None and corridor_geom.intersects(Point(lon, lat)):
                popup_html = format_osm_popup(tags)
                folium.CircleMarker([lat, lon], radius=6, color="green", fill=True, fill_opacity=0.9,
                                    popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
        elif el["type"] == "way" and "geometry" in el:
            coords = [(pt["lon"], pt["lat"]) for pt in el["geometry"]]
            if len(coords) >= 2 and corridor_geom.intersects(LineString(coords)):
                popup_html = format_osm_popup(tags)
                folium.PolyLine([(lat, lon) for lon, lat in coords], weight=3, color="green",
                                popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)
    return fg


def add_osm_missing_opening_hours(m: folium.Map, data, corridor_geom, group_name="OSM missing opening hours"):
    fg = FeatureGroup(name=group_name, show=False)
    for el in data.get("elements", []):
        tags = el.get("tags", {})
        if not tags:
            continue

        # likely should have opening_hours but missing
        likely_needs_hours = (
            tags.get("amenity") in ["restaurant", "cafe", "bar", "pub", "fast_food"] or
            tags.get("tourism") in ["hotel", "hostel", "motel", "guest_house", "information"] or
            tags.get("shop") is not None or
            tags.get("tourism") == "rental"
        )
        if not likely_needs_hours or "opening_hours" in tags:
            continue

        if el["type"] == "node":
            lat, lon = el.get("lat"), el.get("lon")
            if lat is not None and lon is not None and corridor_geom.intersects(Point(lon, lat)):
                popup_html = format_osm_popup(tags)
                folium.CircleMarker([lat, lon], radius=6, color="red", fill=True, fill_opacity=0.9,
                                    popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
        elif el["type"] == "way" and "geometry" in el:
            coords = [(pt["lon"], pt["lat"]) for pt in el["geometry"]]
            if len(coords) >= 2 and corridor_geom.intersects(LineString(coords)):
                popup_html = format_osm_popup(tags)
                folium.PolyLine([(lat, lon) for lon, lat in coords], weight=3, color="red",
                                popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)
    return fg






In [3]:
# ========================
# Wikidata Popups
# ========================
def format_wikidata_popup(it):
    label = it.get("label") or it["item"].split("/")[-1]
    desc = it.get("description") or ""

    img_html = ""
    if it.get("image"):
        img_html = f"<img src='{it['image']}' width='200' style='margin-bottom:6px;'><br>"
    elif it.get("commonscat"):
        cat = it['commonscat'].replace(" ", "_")
        img_html = f"<img src='https://commons.wikimedia.org/wiki/Special:FilePath/{cat}?width=200' width='200' style='margin-bottom:6px;'><br>"

    links = [f"🗺️ <a href='{it['item']}' target='_blank'>Wikidata</a>"]
    if it.get("svwiki"): links.append(f"📖 <a href='{it['svwiki']}' target='_blank'>Wikipedia</a>")
    if it.get("commonscat"): links.append(f"🖼️ <a href='https://commons.wikimedia.org/wiki/Category:{it['commonscat']}' target='_blank'>Commons</a>")
    if it.get("website"): links.append(f"🌐 <a href='{it['website']}' target='_blank'>Website</a>")
    if it.get("naturkartan"): links.append(f"🧭 <a href='https://naturkartan.se/sv/places/{it['naturkartan']}' target='_blank'>Naturkartan</a>")
    if it.get("inatplace"): links.append(f"🌱 <a href='https://www.inaturalist.org/places/{it['inatplace']}' target='_blank'>iNaturalist</a>")
    if it.get("instaplace"): links.append(f"📍 <a href='https://www.instagram.com/explore/locations/{it['instaplace']}/' target='_blank'>Instagram Place</a>")
    if it.get("instagram"): links.append(f"📷 <a href='https://www.instagram.com/{it['instagram']}/' target='_blank'>Instagram</a>")
    if it.get("twitter"): links.append(f"🐦 <a href='https://x.com/{it['twitter']}' target='_blank'>Twitter/X</a>")
    if it.get("facebook"): links.append(f"👥 <a href='https://www.facebook.com/{it['facebook']}' target='_blank'>Facebook</a>")
    if it.get("gmapid"): links.append(f"📍 <a href='https://www.google.com/maps/place/?cid={it['gmapid']}' target='_blank'>Google Maps</a>")

    html = f"""
    <div style='min-width:240px;font-family:sans-serif;font-size:13px;'>
        <h4 style='margin:0 0 6px 0;'>{label}</h4>
        {img_html}
        <p style='margin:0 0 6px 0;'><em>{desc}</em></p>
        <p style='margin:0;'>{' | '.join(links)}</p>
    </div>
    """
    return html


# ========================
# Map Layers
# ========================
def add_wikidata_layer(m: folium.Map, items, group_name="Wikidata (P6104)"):
    fg = FeatureGroup(name=group_name, show=True)
    for it in items:
        if it["latlon"]:
            lat, lon = it["latlon"]
            popup_html = format_wikidata_popup(it)
            folium.CircleMarker([lat, lon], radius=5, color="blue", fill=True, fill_opacity=0.7,
                                popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)


def add_wikidata_social_layer(m: folium.Map, items, group_name="Wikidata with online presence"):
    fg = FeatureGroup(name=group_name, show=False)
    for it in items:
        if it["latlon"] and any([it.get("website"), it.get("inatplace"), it.get("instaplace"),
                                 it.get("gmapid"), it.get("naturkartan"),
                                 it.get("instagram"), it.get("twitter"), it.get("facebook")]):
            lat, lon = it["latlon"]
            popup_html = format_wikidata_popup(it)
            folium.CircleMarker([lat, lon], radius=6, color="purple", fill=True, fill_opacity=0.8,
                                popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)


def add_osm_objects_layer(m, data, corridor_geom, group_name="OSM objects in 300 m corridor"):
    fg = FeatureGroup(name=group_name, show=True)
    for el in data.get("elements", []):
        tags = el.get("tags", {})
        if not tags: continue
        if el["type"] == "node":
            lat, lon = el["lat"], el["lon"]
            popup_html = format_osm_popup(tags, el["type"], el["id"])
            folium.CircleMarker([lat, lon], radius=3, color="black", fill=True, fill_opacity=0.6,
                                popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)


def add_osm_social_layer(m, data, corridor_geom, group_name="OSM with online presence"):
    fg = FeatureGroup(name=group_name, show=False)
    for el in data.get("elements", []):
        tags = el.get("tags", {})
        if not tags: continue
        if any(k in tags for k in ["contact:facebook", "contact:instagram", "contact:twitter", "website"]):
            if el["type"] == "node":
                lat, lon = el["lat"], el["lon"]
                popup_html = format_osm_popup(tags, el["type"], el["id"])
                folium.CircleMarker([lat, lon], radius=5, color="orange", fill=True, fill_opacity=0.8,
                                    popup=folium.Popup(popup_html, max_width=320)).add_to(fg)
    fg.add_to(m)


def add_osm_opening_layers(m, data, corridor_geom):
    fg_has = FeatureGroup(name="OSM with opening hours", show=False)
    fg_missing = FeatureGroup(name="OSM missing opening hours", show=False)

    candidates = ["restaurant", "cafe", "fast_food", "pub", "bar", "hotel", "guest_house", "hostel",
                  "car_rental", "bicycle_rental", "boat_rental", "canoe_rental", "kayak_rental"]

    for el in data.get("elements", []):
        tags = el.get("tags", {})
        if not tags: continue
        amenity = tags.get("amenity") or tags.get("tourism") or tags.get("shop")
        if not amenity: continue

        lat, lon = el.get("lat"), el.get("lon")
        if not (lat and lon): continue

        if amenity in candidates:
            popup_html = format_osm_popup(tags, el["type"], el["id"])
            if "opening_hours" in tags:
                folium.CircleMarker([lat, lon], radius=6, color="green", fill=True, fill_opacity=0.8,
                                    popup=folium.Popup(popup_html, max_width=320)).add_to(fg_has)
            else:
                folium.CircleMarker([lat, lon], radius=6, color="red", fill=True, fill_opacity=0.8,
                                    popup=folium.Popup(popup_html, max_width=320)).add_to(fg_missing)

    fg_has.add_to(m)
    fg_missing.add_to(m)


def add_trail_layer(m, lines, group_name="SAT trail (from GeoJSON)"):
    fg = FeatureGroup(name=group_name, show=True)
    for ln in lines:
        latlons = [(y, x) for x, y in ln.coords]
        popup_html = """
        <div style='font-family:sans-serif;font-size:13px;'>
          <b>Stockholm Archipelago Trail</b><br>
          <a href='https://stockholmarchipelagotrail.com/' target='_blank'>🇸🇪 Official (Swedish)</a> | 
          <a href='https://stockholmarchipelagotrail.com/en/' target='_blank'>🇬🇧 Official (English)</a>
        </div>
        """
        folium.PolyLine(latlons, weight=4, opacity=0.8, color="red",
                        popup=folium.Popup(popup_html, max_width=300)).add_to(fg)
    fg.add_to(m)
    return fg


def add_corridor_layer(m, corridor_geom, group_name="Corridor (300m)"):
    fg = FeatureGroup(name=group_name, show=False)
    polys = [corridor_geom] if isinstance(corridor_geom, Polygon) else list(corridor_geom.geoms)
    for poly in polys:
        coords_latlon = [(lat, lon) for lon, lat in poly.exterior.coords]
        folium.Polygon(coords_latlon, color="green", weight=2, fill=True, fill_opacity=0.1).add_to(fg)
    fg.add_to(m)
    return fg


# ========================
# UI Boxes
# ========================
class FixedMacroElement(MacroElement):
    def __init__(self, tpl, name="macro_element"):
        super().__init__()
        self._template = Template(tpl)
        self._name = name 
        
def add_about_box(m, issue_number=217, map_name="SAT_wikipedia_OSM", repo="salgo60/Stockholm_Archipelago_Trail"):
    from datetime import datetime
    created_date = datetime.now().strftime("%Y-%m-%d %H:%M")
    issue_url = f"https://github.com/{repo}/issues/{issue_number}"

    tpl = f"""
    {{% macro html(this, kwargs) %}}
    <div style="position: fixed; top: 70px; left: 10px; z-index:9999;
                background: white; border:2px solid #666; border-radius:8px;
                padding: 8px; font-size:13px; box-shadow: 2px 2px 6px rgba(0,0,0,.3);
                max-width: 300px;">
      <details open>
        <summary style="cursor:pointer;font-weight:600;">ℹ️ About</summary>
        <div style="margin-top:6px;">
          <b>{map_name}</b><br>
          Created: {created_date}<br>
          Issue: <a href="{issue_url}" target="_blank">#{issue_number}</a><br>
          <div style="margin-top:6px;">
            <a href="https://youtu.be/_nbI8hkRAvA" target="_blank">▶️ video about the map</a><br>
            <a href="https://raw.githack.com/salgo60/Stockholm_Archipelago_Trail/main/notebook/output/SAT_ALL_IN_ONE_142_3_dashboard_latest.html" target="_blank">📊 SAT Dashboard</a><br>
            <a href="https://github.com/{repo}/issues?q=is%3Aissue" target="_blank">🐛 Project repo issues</a><br>
            <a href="https://www.openstreetmap.org/relation/19012437" target="_blank">🗺️ Trail on OSM</a><br>
            <a href="https://commons.wikimedia.org/wiki/Category:Stockholm_Archipelago_Trail" target="_blank">🖼️ Trail on Wikicommons</a><br>
            <a href="https://stockholmarchipelagotrail.com/" target="_blank">🌐 Official page</a><br>
            <a href="https://www.facebook.com/groups/2875020699552247" target="_blank">👥 Unofficial FB group</a><br>
            <a href="https://traveltrade.visitsweden.com/plan/news-sweden/Stockholm-Archipelago-Trail/" target="_blank">🇸🇪 Visit Sweden</a>
          </div>
        </div>
      </details>
    </div>
    {{% endmacro %}}
    """
    m.get_root().add_child(FixedMacroElement(tpl, name="about_box"))


def add_legend_box(m):
    legend_items = """
    🔵 Wikidata items<br>
    🟣 Wikidata with online presence<br>
    🔴 Trail line<br>
    🟩 Corridor polygon<br>
    ⚫ OSM objects<br>
    🟠 OSM with online presence<br>
    🟢 OSM with opening hours<br>
    🔴 OSM missing opening hours
    """
    tpl = f"""
    {{% macro html(this, kwargs) %}}
    <div style="position: fixed; bottom: 30px; left: 30px; z-index:9999;
                background: white; border:2px solid #666; border-radius:8px;
                padding: 8px; font-size:13px; box-shadow: 2px 2px 6px rgba(0,0,0,.3);
                max-width: 220px;">
      <details open>
        <summary style="cursor:pointer; font-weight:600;">📍 Legend</summary>
        <div style="margin-top:6px;">{legend_items}</div>
      </details>
    </div>
    {{% endmacro %}}
    """
    m.get_root().add_child(FixedMacroElement(tpl, name="legend_box"))

def add_stats_box(m, map_name: str, wd_count: int, osm_raw: int, osm_filtered: int, from_cache: bool = False):
    source = "cache" if from_cache else "Overpass"
    tpl = f"""
    {{% macro html(this, kwargs) %}}
    <div style="position: fixed; bottom: 30px; right: 30px; z-index:9999;
            background: white; border:2px solid #666; border-radius:8px;
            padding: 8px; font-size:13px; box-shadow: 2px 2px 6px rgba(0,0,0,.3);
            max-width: 260px;">
        <details>
            <summary style="cursor:pointer;font-weight:600;">📊 Status</summary>
            <div style="margin-top:6px;">
              <b>{map_name}</b><br>
              Wikidata items: {wd_count}<br>
              OSM fetched: {osm_raw}<br>
              OSM in corridor: {osm_filtered}<br>
              Source: {source}
            </div>
        </details>
    </div>
    {{% endmacro %}}
    """
    m.get_root().add_child(FixedMacroElement(tpl, name="stats_box"))


# ========================
# Build Map
# ========================
m = folium.Map(location=MAP_CENTER, zoom_start=MAP_ZOOM, tiles="OpenStreetMap")
Fullscreen().add_to(m)
MeasureControl(position='topleft', primary_length_unit='meters').add_to(m)
MousePosition(position='bottomright', empty_string='NaN', prefix='Lat/Lng:', num_digits=5).add_to(m)

# Wikidata
print("Fetching Wikidata items…")
wd_items = wikidata_items_with_social(lang="sv")
add_wikidata_layer(m, wd_items)
add_wikidata_social_layer(m, wd_items)

# Trail + Corridor
lines = get_trail_geometry_from_geojson(GEOJSON_PATH)
corridor_geom = corridor_from_lines_wgs84(lines, BUFFER_METERS_EACH_SIDE)

all_coords = [(x, y) for ln in lines for x, y in ln.coords]
minlon, maxlon = min(x for x, y in all_coords), max(x for x, y in all_coords)
minlat, maxlat = min(y for x, y in all_coords), max(y for x, y in all_coords)

# OSM fetch/cache
osm_data, from_cache = load_or_fetch_filtered_osm(minlat, minlon, maxlat, maxlon, corridor_geom, reload_osm=False)
osm_filtered_count = len(osm_data["elements"])

add_osm_objects_layer(m, osm_data, corridor_geom)
add_osm_social_layer(m, osm_data, corridor_geom)
add_osm_opening_layers(m, osm_data, corridor_geom)

add_trail_layer(m, lines)
add_corridor_layer(m, corridor_geom)

# UI
add_about_box(m)
add_legend_box(m)
add_stats_box(m, "SAT_wikipedia_OSM", len(wd_items), len(osm_data["elements"]), osm_filtered_count, from_cache)

folium.LayerControl(collapsed=False).add_to(m)
display(m)


Fetching Wikidata items…
Loading filtered OSM data from cache: osm_filtered_cache.json


In [4]:
import shutil
from pathlib import Path

def _to_latest_name(filename: str | Path) -> Path:
    p = Path(filename)
    stem = p.stem
    new_stem = re.sub(r'_(?:20\d{6})(?:_\d{4})?$', '', stem)
    return p.with_name(new_stem + "_latest.html")

def save_with_latest(map_object, filename: str | Path):
    map_object.save(str(filename))
    latest_path = _to_latest_name(filename)
    shutil.copyfile(filename, latest_path)
    print(f"Saved: {filename}\nUpdated: {latest_path}")

In [5]:
import pandas as pd
import re
project_name = "SAT_217_Wikipedia_OSM" 
OUTPUT_DIR = "./output"
stamp = pd.Timestamp.now().strftime("%Y%m%d_%H%M")
html_path = os.path.join(OUTPUT_DIR, f"{project_name}_{stamp}.html")

save_with_latest(m, html_path)



Saved: ./output/SAT_217_Wikipedia_OSM_20251002_1503.html
Updated: output/SAT_217_Wikipedia_OSM_latest.html


In [6]:
from datetime import datetime
# End timer and calculate duration
end_time = time.time()
elapsed_time = end_time - start_time# Bygg audit-lager för den här etappen

# Print current date and total time
now = datetime.now().strftime("%Y-%m-%d %H:%M")
print("Date:", datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
minutes, seconds = divmod(elapsed_time, 60)
print("Total time elapsed: {:02.0f} minutes {:05.2f} seconds".format(minutes, seconds))


Date: 2025-10-02 15:03:37
Total time elapsed: 00 minutes 05.70 seconds
